In [1]:
from IPython.display import clear_output, Image, display, HTML

def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = "<stripped %d bytes>"%size
    return strip_def

def show_graph(graph_def = None, max_const_size=32):
    """Visualize TensorFlow graph."""
    
    if graph_def is None:
        graph_def = tf.get_default_graph().as_graph_def()
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))

    iframe = """
        <iframe seamless style="width:1200px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))
    display(HTML(iframe))

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import statistics as stat

import os
import logging
import math
import itertools

import scipy.stats
import typing
import random

import tensorflow as tf
from sklearn.cross_validation import train_test_split

logging.basicConfig(level=logging.DEBUG)

/opt/conda/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
/opt/conda/lib/python3.6/site-packages/sklearn/cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
DEBUG:matplotlib.backends:backend module://ipykernel.pylab.backend_inline version unknown


In [3]:
def calculate_account_value(money, stocks, stock_prices: tf.Tensor):
        """
        Calculates the current Marked Value of the account

        Arguments:
        - stock_prices:  tensor[minibatch, company] -> price

        Returns: 
        - tensor[minibatch] -> Current market value
        """
        with tf.name_scope("account_value"):
            return tf.reduce_sum(money, axis=1) + tf.reduce_sum(stocks*stock_prices, axis=1)

class TradingState(typing.NamedTuple):
    stocks:        tf.Tensor   # tensor[minibatch, company] -> number of stocks
    money:         tf.Tensor   # tensor[minibatch] -> [cash available, cash that will be available tomorrow, ...]
    account_value: tf.Tensor   # tensor[minibatch] -> Market value of account
    inner_state:  typing.Any  # Whatever state the trader want to propagate from one state to the next
        
    

In [4]:
FEATURE_LOW    = 0
FEATURE_HIGH   = 1
FEATURE_OPEN   = 2
FEATURE_CLOSE  = 3
FEATURE_VOLUME = 4

RESPONSE_BUY_PRICE   = 0
RESPONSE_BUY_AMOUNT  = 1
RESPONSE_SELL_LOW    = 2
RESPONSE_SELL_HIGH   = 3

MONEY_TODAY = 0
MONEY_TOMORROW = 1
MONEY_AFTER_TOMORROW = 2

SELL_TRANSACTION_COST = 5 # 5 USD per transaction
BUY_TRANSACTION_COST = 5 # 5 USD per transaction

def build_trader(state: TradingState, historic_data: tf.Tensor, inner_state: typing.Any) -> tf.Tensor:
    """
    Builds the trader network on tensorflow
    
    Arguments:
    - state: Trading state coming from the previous day
    - historic_data: tensor[minibatch, time, company] -> [low, high, open, close]
    
    Returns: 
    tensor[minibatch, company] -> [buy_price, buy_amount, sell_low_price, sell_high_price]
    - buy_price: The price for which you want to buy stocks
    - buy_amount: Fraction of the cash available to be used to buy stocks from this company (If the price target is reached)
    - sell_high_price: If the stock price reaches more than this amount, all of the owned stocks will be sold (Ideal case, sell when the price is high)
    - sell_low_price: If the stock price reaches less than this amount, all of the owned stocks will also be sold (Fucked up case: Prices are crashing, minimize losses)
    """
    
    # FIXME: This is as dumb as it gets! A real neural network should come here
    
    with tf.name_scope('buy_price'):
        buy_price = historic_data[:,-1,:,FEATURE_CLOSE] + 1.2 * (historic_data[:,-1,:,FEATURE_LOW] - historic_data[:,-1,:,FEATURE_OPEN])
    with tf.name_scope('buy_amount'):
        buy_amount = tf.fill(tf.shape(buy_price), value=0.1)
    with tf.name_scope('sell_low_price'):
        sell_low_price = tf.fill(tf.shape(buy_price), value=-1.)  # Never!
    with tf.name_scope('sell_high_price'):
        sell_high_price = historic_data[:,-1,:,FEATURE_CLOSE] + 0.8 * (historic_data[:,-1,:,FEATURE_HIGH] - historic_data[:,-1,:,FEATURE_OPEN])

    return (tf.stack([buy_price, buy_amount, sell_low_price, sell_high_price], axis=2), inner_state)
        

In [5]:
def build_env_step(state: TradingState, historic_data: tf.Tensor, next_day_data: tf.Tensor) -> TradingState:
    """
    Builds a single-day trading environment.
    Arguments:
    - state: Trading state coming from the previous day
    - historic_data: tensor[minibatch, time, company] -> [low, high, open, close]
    - next_day_data: tensor[minibatch, company] -> [low, high, open, close]

    
    Returns: The next state, computed at the end of the next trading day
    """   
    with tf.name_scope("trader"):
        trader, new_inner_state = build_trader(state = state, historic_data = historic_data, inner_state = state.inner_state)

    def smooth_lte(a, b):
        return tf.where(a <= b, tf.ones(tf.shape(a)), tf.zeros(tf.shape(a)))
    def smooth_gte(a, b):
        return tf.where(a >= b, tf.ones(tf.shape(a)), tf.zeros(tf.shape(a)))
        
    with tf.name_scope("simulator"):
        with tf.name_scope("slicing"):
            buy_price       = trader[:,:, RESPONSE_BUY_PRICE]
            buy_amount      = trader[:,:, RESPONSE_BUY_AMOUNT]
            sell_low_price  = trader[:,:, RESPONSE_SELL_LOW]
            sell_high_price = trader[:,:, RESPONSE_SELL_HIGH]
            current_money   = state.money[:, MONEY_TODAY]
            current_stocks  = state.stocks
            eod_stock_prices = next_day_data[:, :, FEATURE_CLOSE]

        # Executes SELL transactions if prices reaches BELOW a threshold (minimize losses)            
        # (If the day opens below the threshold for LOW SELL, use the open price)
        with tf.name_scope("sell_low"):
            will_sell_low         = smooth_lte(next_day_data[:, :, FEATURE_LOW],  sell_low_price)
            will_sell_low         = tf.where(current_stocks <= 0, tf.zeros(tf.shape(will_sell_low)), will_sell_low)
            actual_sell_low_price = sell_low_price # FIXMEtf.min(next_day_data[:, :, FEATURE_OPEN], sell_low_price)
            money_earned_sell_low = tf.reduce_sum(will_sell_low * (actual_sell_low_price * current_stocks), axis=1)
            money_spent_sell_low  = tf.reduce_sum(will_sell_low * SELL_TRANSACTION_COST, axis=1)
            current_stocks        = (1 - will_sell_low) * current_stocks
            kernel                 = tf.identity(will_sell_low, 'kernel')

        # Executes SELL transactions if prices reaches ABOVE a threshold (Maximize gains)
        with tf.name_scope("sell_high"):
            will_sell_high         = smooth_gte(next_day_data[:, :, FEATURE_HIGH], sell_high_price)
            will_sell_high         = tf.where(current_stocks <= 0, tf.zeros(tf.shape(will_sell_high)), will_sell_high)
            money_earned_sell_high = tf.reduce_sum(will_sell_high * (sell_high_price * current_stocks), axis=1)
            money_spent_sell_high  = tf.reduce_sum(will_sell_high * SELL_TRANSACTION_COST, axis=1)
            current_stocks         = (1 - will_sell_high) * current_stocks
            kernel                 = tf.identity(will_sell_high, 'kernel')

        # Executes BUY transactions if prices reaches above a threshold
        # (Normalize `buy_amount` to be in amount of stocks, instead of fraction of my money)
        with tf.name_scope("buy"):
            buy_amount       = buy_amount * current_money[:, tf.newaxis] / buy_price # TODO: Floor -- Can only buy integer number of stocks
            will_buy         = smooth_lte(next_day_data[:, :, FEATURE_LOW], buy_price)
            will_buy         = tf.where(buy_amount <= 0, tf.zeros(tf.shape(will_buy)), will_buy)
            money_spent_buy  = tf.reduce_sum(will_buy * ((buy_price * buy_amount) + BUY_TRANSACTION_COST), axis=1)
            current_stocks   = current_stocks + will_buy * buy_amount            
            kernel           = tf.identity(will_buy, 'kernel')

        with tf.name_scope("update_money"):
            with tf.name_scope("money_spent"):
                money_spent = money_spent_sell_low + money_spent_sell_high + money_spent_buy
            with tf.name_scope("money_earned"):
                money_earned = money_earned_sell_low + money_earned_sell_high
            
            new_money_first = tf.expand_dims(current_money + state.money[:, MONEY_TOMORROW] - money_spent, axis = 1)
            new_money_middle = state.money[:, 2:]
            new_money_last = tf.expand_dims(money_earned, axis = 1)
            
            next_money = tf.concat([
                new_money_first,
                new_money_middle,
                new_money_last
            ], axis = 1)
            #print(f"MONEY - IN: {state.money.shape}")#, OUT: {next_money.shape}")
            #print(f"current_money:{current_money.shape}, money_spent:{money_spent.shape}, money_earned_low:{money_earned_low.shape}, money_earned_high:{money_earned_high.shape}")
            #print(f"new_first:{new_money_first.shape}, new_middle:{new_money_middle.shape}, new_last:{new_money_last.shape}, money_earned_high:{money_earned_high.shape}")
            #print(f"MONEY - OUT: {next_money.shape}")
            
        return TradingState(
            stocks = current_stocks,
            money = next_money,
            account_value = calculate_account_value(next_money, current_stocks, eod_stock_prices),
            inner_state = new_inner_state
        )       
        

In [6]:
def build_env(historic_data, initial_state, num_days, historic_window_size):    
    with tf.name_scope(f'state_0'):
        current_state = TradingState(
            stocks = tf.identity(initial_state.stocks, name='stocks'),
            money = tf.identity(initial_state.money, name='money'),
            account_value = tf.identity(initial_state.account_value, name='account_value'),
            inner_state = None
        )
    all_states = [current_state]
        
    for i in range(num_days):
        #print(f'day_{i}')
        with tf.name_scope(f'day_{i}'):
            with tf.name_scope(f'historic_data'):
                historic_slice = historic_data[:, i:i+historic_window_size, : ,:]
            with tf.name_scope(f'next_day_data'):
                next_day_slice = historic_data[:, i+historic_window_size, : ,:]

            current_state = build_env_step(
                state = current_state,
                historic_data = historic_slice,
                next_day_data = next_day_slice
            )
            
        with tf.name_scope(f'state_{i+1}'):
            current_state = TradingState(
                stocks = tf.identity(current_state.stocks, name='stocks'),
                money = tf.identity(current_state.money, name='money'),
                account_value = tf.identity(current_state.account_value, name='account_value'),
                inner_state = None
            )

        all_states.append(current_state)
    return all_states

In [28]:
def build_graph(warmup_days = 10, evaluated_days = 30, historic_window_size = 5, money_settle_time = 3) -> tf.Graph:
    total_days = evaluated_days + warmup_days + historic_window_size
    
    graph = tf.Graph()
    with graph.as_default():
        with tf.name_scope("inputs"):
            stock_history = tf.placeholder(tf.float32, shape=(None, total_days, None, 5), name="stock_history")

            minibatch_size = tf.shape(stock_history)[0]
            num_companies = tf.shape(stock_history)[2]    
            default_initial_stocks = tf.zeros([minibatch_size, num_companies], name = 'default_initial_stocks')
            initial_stocks = tf.placeholder_with_default(default_initial_stocks, shape = (None, None), name = 'initial_stocks')

            initial_money_simple = tf.placeholder_with_default(10000., shape = (), name = 'initial_money_simple')
            default_initial_money = tf.concat(
                [
                    initial_money_simple * tf.ones([minibatch_size, 1]),
                    tf.zeros([minibatch_size, money_settle_time-1])
                ], 
                axis = 1,
                name = 'default_initial_money')
            initial_money = tf.placeholder_with_default(default_initial_money, shape = (None, money_settle_time), name = 'initial_money')

            initial_stock_prices = stock_history[:, historic_window_size - 1, :, FEATURE_CLOSE]
            
            initial_state = TradingState(
                stocks = initial_stocks,
                money = initial_money,
                account_value = calculate_account_value(initial_money, initial_stocks, initial_stock_prices),
                inner_state = None
            )

        with tf.name_scope("trading"):
            all_states = build_env(stock_history, initial_state, warmup_days + evaluated_days, historic_window_size)

        with tf.name_scope("evaluation"):
            with tf.name_scope("initial_value"):
                initial_value = all_states[warmup_days].account_value
            with tf.name_scope("final_value"):
                final_value = all_states[-1].account_value
            with tf.name_scope("normalized_profit"):
                  # Normalizes using 100*ln(x) -- It's the same as percentage variation for small values, and log-scaled for larger ones
                normalized_profit = 100*tf.log(final_value / initial_value) / evaluated_days
                normalized = tf.identity(normalized_profit, name="values")
                normalized_profit_mean = tf.reduce_mean(normalized_profit, axis = 0, name = 'mean')
                #with tf.name_scope("stderr"):
                #    a = tf.reduce_sum(tf.square(normalized_profit - normalized_profit_mean), axis = 0)
                #    b = tf.shape(normalized_profit)[0]# - tf.constant(1.)
                #    c = tf.div(a, b)
                #    normalized_profit_stderr = tf.sqrt(c)
                #    normalized_profit_stderr = normalized_profit_mean * 2.

    return graph    

In [8]:
graph = build_graph()
show_graph(graph)

In [13]:
DATASET_DIR = "dataset/dataset-2017-10-11"
STOCK_DIR = f"{DATASET_DIR}/Stocks"
ETF_DIR = f"{DATASET_DIR}/ETFs"

sp500 = pd.read_csv('dataset/s&p500.tsv', sep='\t')['Ticker symbol']

def concat_datasets(datasets):
    return pd.concat(
        df.assign(Symbol = symbol)
        for symbol, df in datasets.items()
    )

def dataset_to_timeseries(df, days):
    """
    Concatenates `days` sequential values to create a larger feature array.
    """
    parallel_series = [
        df[d:len(df)+1-days+d]
        for d in reversed(range(days))
    ]
    
    cols = ['Date']
    data = [parallel_series[0].Date]
    for i in range(len(parallel_series)):
        s = parallel_series[i]
        for col in ['Open', 'Close', 'High', 'Low', 'Volume']:
            cols.append(f'{col}.{i}')
            data.append(s[col])
            
    return pd.DataFrame(list(zip(*data)), columns=cols)

def split_dataset_by_date(dataset, test_size = 0.2):
    trading_dates = sorted(set(dataset.Date))
    train_dates, test_dates = train_test_split(trading_dates, test_size=test_size)
    train_dataset = dataset[dataset.Date.isin(set(train_dates))].sample(frac=1).reset_index(drop=True)
    test_dataset = dataset[dataset.Date.isin(set(test_dates))].sample(frac=1).reset_index(drop=True)
    return (train_dataset, test_dataset)

def extract_all_data(symbols, feature_days=45, min_date='1990-01-01'):
    symbols = set(symbols)
    failed_csvs = []
    raw_data = {}
    timeseries_feature_data = {}
    for filename in os.listdir(STOCK_DIR):
        symbol = filename.split('.')[0].upper()
        if not symbol in symbols:
            continue

        raw = pd.read_csv(f"{STOCK_DIR}/{filename}")
        raw_data[symbol] = raw[raw.Date >= min_date]
        timeseries_feature_data[symbol] = dataset_to_timeseries(raw_data[symbol], feature_days)

        #if len(raw_data) > 5:
            #break
            
    if failed_csvs:
        logging.warning(f'Failed to read {len(failed_csvs)} CSV files: {failed_csvs}')
            
    all_samples = concat_datasets(timeseries_feature_data)
    train_samples, test_samples = split_dataset_by_date(all_samples)
    return train_samples, test_samples

def create_minibatch(dataset, minibatch_size, num_companies):
    minibatch = []
    for i in range(minibatch_size):
        date = random.choice(dataset.Date)
        dataset_at_date = dataset[dataset.Date == date]

        samples = dataset_at_date.sample(n = num_companies, replace = True)
        samples = samples.as_matrix(columns=samples.columns[1:-1])
        samples = samples.reshape([num_companies, -1, 5])
        samples = samples.transpose((1,0,2))
        minibatch.append(samples)
    return np.stack(minibatch)
    
def minibatch_producer(symbols, feature_days=45, min_date='2010-01-01', minibatch_size=10, num_companies=10):
    all_data = extract_all_data(symbols, feature_days=feature_days, min_date=min_date)
    def produce(train=True, minibatch_size=minibatch_size, num_companies=num_companies):
        return create_minibatch(dataset=all_data[0 if train else 1], minibatch_size=minibatch_size, num_companies=num_companies)
    return produce

next_minibatch = minibatch_producer(sp500[:20])

In [30]:
with build_graph().as_default():
    with tf.Session() as sess:
        tf.global_variables_initializer().run()
        #print(stock_history.eval(feed_dict={stock_history: np.zeros(4, 2)}))
        #bah = tf.placeholder(tf.float32, shape=(3,2), name="bah")
        bah = tf.placeholder_with_default([[3]], shape=(None, None), name="bah")
        #print(initial_stocks.eval(feed_dict={stock_history: 100*np.ones([3, total_days, 8, 4]), initial_stocks: np.ones([12,8])}))

        defaults = {
            tf.get_default_graph().get_tensor_by_name('inputs/stock_history:0'): next_minibatch(minibatch_size=100, num_companies=10),
            #initial_stocks: [[1,2,3],[4,5,6]],
            tf.get_default_graph().get_tensor_by_name('inputs/initial_money_simple:0'): 50000
            #initial_money: [[500,100,50],[1000,0,100]],
        }

        for i in range(15):
            #print(f'============{i}==============')
            account_value = tf.get_default_graph().get_tensor_by_name(f'trading/state_{i}/account_value:0')
            stocks = tf.get_default_graph().get_tensor_by_name(f'trading/state_{i}/stocks:0')
            money = tf.get_default_graph().get_tensor_by_name(f'trading/state_{i}/money:0')
            
            will_buy = tf.get_default_graph().get_tensor_by_name(f'trading/day_{i}/simulator/buy/kernel:0')
            will_sell_low = tf.get_default_graph().get_tensor_by_name(f'trading/day_{i}/simulator/sell_low/kernel:0')
            will_sell_high = tf.get_default_graph().get_tensor_by_name(f'trading/day_{i}/simulator/sell_high/kernel:0')

            def ev(x):
                return x.eval(feed_dict=defaults)
            args = dict(feed_dict=defaults)
            
            #print(f'account_value: {ev(account_value)}')
            #print(f'money: {ev(money)}')
            #print(f'stocks: {ev(stocks)}')
            #print(f'will_buy: {ev(will_buy)}')
            #print(f'will_sell_low: {ev(will_sell_low)}')
            #print(f'will_sell_high: {ev(will_sell_high)}')
            #trading/day_{i}/simulator/buy/kernel
        normalized_evaluations = tf.get_default_graph().get_tensor_by_name('evaluation/normalized_profit/values:0')
        normalized_evaluation_values = ev(normalized_evaluations)
        print(f'trader_evaluation: {normalized_evaluation_values.mean():.2f}±{normalized_evaluation_values.std():.2f} %/day')
        #print(graph_evaluation.eval(feed_dict=defaults))
        #print(initial_money.eval(feed_dict=defaults))
        #print(initial_stocks.eval(feed_dict=defaults))
        #sess.run(stock_history.shape[0])

        #value = account_value(stock_history[:, -1, :, FEATURE_CLOSE], initial_stocks, initial_money)
        #print(value.eval(feed_dict=defaults))


trader_evaluation: -0.18±0.08 %/day
